앞에 (1)파일과 연결해서 쓰세요

In [5]:
# 차트 3: 에란겔 피처 박스플롯 (페르소나별 분포)
if len(df_erangel) > 0:
    # cluster >= 0 → segment != 'uncertain'
    df_box = df_erangel[df_erangel['segment'] != 'uncertain'].copy()

    feature_display = {
        'drop_distance_from_path': '낙하 거리 (m)',
        'early_enemy_density':     '초기 적 밀도 (명)',
        'vehicle_use_ratio':       '차량 이용률',
        'bluezone_exposure_ratio': '블루존 노출률',
        'kill_rate':               '분당 킬',
        'safezone_edge_ratio':     '외곽 포지셔닝 비율',
    }
    available = {k: v for k, v in feature_display.items() if k in df_box.columns}

    n_cols = 3
    n_rows = (len(available) + n_cols - 1) // n_cols

    fig = make_subplots(rows=n_rows, cols=n_cols,
                        subplot_titles=list(available.values()))

    palette  = px.colors.qualitative.Set2
    personas = sorted(df_box['persona'].dropna().unique())

    for idx, (feat, feat_name) in enumerate(available.items()):
        row = idx // n_cols + 1
        col = idx % n_cols + 1
        for j, persona in enumerate(personas):
            sub = df_box[df_box['persona'] == persona][feat].dropna()
            color = PERSONA_COLORS.get(persona, palette[j % len(palette)])
            fig.add_trace(go.Box(
                y=sub,
                name=persona,
                marker_color=color,
                legendgroup=persona,
                showlegend=(idx == 0),
                boxmean=True,
            ), row=row, col=col)

    fig.update_layout(
        title='에란겔 — 클러스터별 피처 분포',
        title_font_size=16,
        height=700,
        width=1100,
        legend_title='전략 유형',
    )
    fig.show()
    fig.write_html(os.path.join(OUTPUT_DIR, 'feature_boxplot.html'))
    print('저장: feature_boxplot.html')

저장: feature_boxplot.html


In [10]:
# 차트 4: 페르소나별 성과 요약 테이블
if len(df_all) > 0 and 'win_flag' in df_all.columns:
    # cluster >= 0 → segment != 'uncertain'
    df_valid = df_all[df_all['segment'] != 'uncertain'].copy()

    perf = (
        df_valid
        .groupby('persona')
        .agg(
            플레이어수  = ('win_flag',     'count'),
            승률      = ('win_flag',     'mean'),
            Top3_비율  = ('top3_flag',   'mean'),
            평균_킬     = ('kills',        'mean'),
            평균_데미지  = ('damageDealt',  'mean'),
            평균_순위   = ('winPlace',     'mean'),
        )
        .round(3)
        .reset_index()
        .sort_values('승률', ascending=False)
    )
    perf['승률']    = perf['승률'].map('{:.1%}'.format)
    perf['Top3_비율'] = perf['Top3_비율'].map('{:.1%}'.format)
    perf['평균_킬']   = perf['평균_킬'].round(2)
    perf['평균_데미지'] = perf['평균_데미지'].round(0).astype(int)
    perf['평균_순위']  = perf['평균_순위'].round(1)

    fig = go.Figure(data=[go.Table(
        header=dict(
            values=list(perf.columns),
            fill_color='#2C3E50',
            align='center',
            font=dict(color='white', size=12),
        ),
        cells=dict(
            values=[perf[col] for col in perf.columns],
            fill_color=[['#ECF0F1' if i % 2 == 0 else 'white'
                         for i in range(len(perf))]] * len(perf.columns),
            align='center',
            font=dict(size=11),
        ),
    )])
    fig.update_layout(
        title='전략 페르소나별 종합 성과 요약 (전 맵 통합)',
        title_font_size=16,
        height=320,
        width=1000,
    )
    fig.show()
    fig.write_html(os.path.join(OUTPUT_DIR, 'persona_summary_table.html'))
    print('저장: persona_summary_table.html')
else:
    print('데이터 없음')

저장: persona_summary_table.html


In [12]:
# 개인 진단 도구
def diagnose_player(account_id, target_map='Erangel'):
    df_target = map_dfs.get(target_map, pd.DataFrame())
    if len(df_target) == 0:
        print(f'{target_map} 데이터 없음')
        return

    rows = df_target[df_target['accountId'] == account_id]
    if len(rows) == 0:
        print(f'플레이어 {account_id} 를 {target_map} 에서 찾을 수 없습니다.')
        return

    p = rows.iloc[0]
    persona = p.get('persona', '알 수 없음')
    segment = p.get('segment', '알 수 없음')
    margin  = p.get('margin', np.nan)

    print('  플레이어 전략 진단')
    print(f'  맵       : {target_map}')
    print(f'  AccountId: {account_id}')
    print(f'  페르소나  : {persona}')
    if pd.notna(margin):
        conf = '높음' if margin >= 1.0 else ('보통' if margin >= 0.5 else '낮음(혼합형)')
        print(f'  분류 신뢰도: {margin:.2f}  ({conf})')
    print('-' * 55)
    print('  [전략 지표]')

    metrics = [
        ('낙하 거리',       'drop_distance_from_path',  '{:.0f}m'),   # m 단위
        ('초기 적 밀도',    'early_enemy_density',      '{:.1f}명'),
        ('로테이션 타이밍', 'rotation_timing_score',    '{:.3f}  (낮을수록 선점)'),
        ('차량 이용률',     'vehicle_use_ratio',         '{:.1%}'),
        ('블루존 노출률',   'bluezone_exposure_ratio',   '{:.1%}'),
        ('안전구역 거리',   'safezone_proximity_mean',   '{:.0f}m'),   # m 단위
        ('외곽 포지션',     'safezone_edge_ratio',       '{:.3f}'),
        ('고도 변화량',     'altitude_variance',         '{:.1f}'),    # 단위 제거
        ('분당 킬',         'kill_rate',                 '{:.3f}'),
        ('이동 속도',       'move_speed',                '{:.2f}m/s'),
        ('힐+부스터',       'heal_boost_use',            '{:.1f}개'),
    ]
    for label, col, fmt in metrics:
        val = p.get(col)
        if val is not None and pd.notna(val):
            print(f'  {label:<16}: {fmt.format(val)}')

    if 'win_flag' in p.index and pd.notna(p['win_flag']):
        print('  [이 판 결과]')
        print(f'  우승 여부: {"우승 🏆" if p["win_flag"] == 1 else "탈락"}')
        if 'winPlace'    in p.index and pd.notna(p['winPlace']):
            print(f'  최종 순위: {int(p["winPlace"])}위')
        if 'kills'       in p.index and pd.notna(p['kills']):
            print(f'  킬       : {p["kills"]:.0f}킬')
        if 'damageDealt' in p.index and pd.notna(p['damageDealt']):
            print(f'  데미지   : {p["damageDealt"]:.0f}')

    # uncertain 제외한 동일 페르소나 플레이어와 비교
    peers = df_target[
        (df_target['persona'] == persona) &
        (df_target['segment'] != 'uncertain') &
        (df_target['accountId'] != account_id)
    ]
    if len(peers) > 0 and 'win_flag' in peers.columns:
        print(f'  [동일 페르소나 평균  n={len(peers):,}명]')
        print(f'  평균 우승률: {peers["win_flag"].mean():.1%}')
        if 'kills' in peers.columns:
            print(f'  평균 킬    : {peers["kills"].mean():.2f}')
        if 'kill_rate' in peers.columns:
            print(f'  평균 분당킬: {peers["kill_rate"].mean():.3f}')


# 샘플 accountId 출력 및 테스트
print('사용법: diagnose_player("account.xxxx", "Erangel")')
print()
if 'Erangel' in map_dfs:
    # uncertain 제외한 플레이어 샘플
    samples = (
        map_dfs['Erangel'][map_dfs['Erangel']['segment'] != 'uncertain']
        ['accountId'].dropna().unique()[:5]
    )
    print('샘플 accountId (uncertain 제외):')
    for s in samples:
        print(f'  {s}')
    print()
    if len(samples) > 0:
        diagnose_player(samples[0], 'Erangel')

사용법: diagnose_player("account.xxxx", "Erangel")

샘플 accountId (uncertain 제외):
  account.00ae636f3f29443490716d28017686d2
  account.04550355e52549ea99457094928c0316
  account.1ddef90833c34149a8aeef6d6b566e26
  account.23931a30c48041c180cccabc6d663610
  account.263c3e56b22c4f3d8066119499641066

  플레이어 전략 진단
  맵       : Erangel
  AccountId: account.00ae636f3f29443490716d28017686d2
  페르소나  : 🌿 외곽 운영형
  분류 신뢰도: 2.17  (높음)
-------------------------------------------------------
  [전략 지표]
  낙하 거리           : 1545m
  초기 적 밀도         : 0.0명
  로테이션 타이밍        : 0.635  (낮을수록 선점)
  차량 이용률          : 17.2%
  블루존 노출률         : 12.6%
  안전구역 거리         : 1177m
  외곽 포지션          : 0.007
  고도 변화량          : 1430.4
  분당 킬            : 0.105
  이동 속도           : 2.40m/s
  힐+부스터           : 10.0개
  [이 판 결과]
  우승 여부: 탈락
  최종 순위: 2위
  킬       : 3킬
  데미지   : 250
  [동일 페르소나 평균  n=42,313명]
  평균 우승률: 6.9%
  평균 킬    : 1.07
  평균 분당킬: 0.055


In [14]:
# 핵심 인사이트 요약
if len(df_all) > 0 and 'win_flag' in df_all.columns:
    # cluster >= 0 → segment != 'uncertain'
    df_valid = df_all[df_all['segment'] != 'uncertain'].copy()

    print('  PUBG 전략 분석 — 핵심 인사이트 요약')

    best = df_valid.groupby('persona')['win_flag'].mean().sort_values(ascending=False)
    print(f'\n[전체 맵 통합 — 페르소나별 우승률]')
    for persona, wr in best.items():
        bar = '█' * int(wr * 200)
        print(f'  {persona:<22}: {wr:.1%}  {bar}')

    print(f'\n[맵별 최고 승률 전략]')
    for map_name, df_m in map_dfs.items():
        # cluster >= 0 → segment != 'uncertain'
        valid = df_m[df_m['segment'] != 'uncertain']
        if len(valid) > 0 and 'win_flag' in valid.columns:
            wr = valid.groupby('persona')['win_flag'].mean()
            if len(wr) > 0:
                print(f'  {map_name:<12}: {wr.idxmax()}  ({wr.max():.1%})')

    if 'damageDealt' in df_valid.columns and 'safezone_proximity_mean' in df_valid.columns:
        print(f'\n[실력(데미지) vs 전략(포지셔닝) — 우승 상관관계]')
        corr_dmg = df_valid['damageDealt'].corr(df_valid['win_flag'])
        corr_pos = df_valid['safezone_proximity_mean'].corr(df_valid['win_flag'])
        corr_kill = df_valid['kill_rate'].corr(df_valid['win_flag']) if 'kill_rate' in df_valid.columns else np.nan
        print(f'  데미지      x 우승: r={corr_dmg:+.3f}')
        print(f'  포지셔닝    x 우승: r={corr_pos:+.3f}')
        if pd.notna(corr_kill):
            print(f'  분당 킬     x 우승: r={corr_kill:+.3f}')
        dominant = '전략(포지셔닝)' if abs(corr_pos) > abs(corr_dmg) else '실력(데미지)'
        print(f'  → {dominant}이 우승에 더 큰 영향')

    # 혼합형 통계
    uncertain_cnt = (df_all['segment'] == 'uncertain').sum()
    print(f'\n[혼합형(uncertain) 현황]')
    print(f'  전체 {len(df_all):,}명 중 {uncertain_cnt:,}명 ({uncertain_cnt/len(df_all):.1%}) 분류 불가')
    print(f'  → MARGIN_THRESHOLD={MARGIN_THRESHOLD} 기준, 낮추면 혼합형 감소')

    print()
    print(f'분석 완료. 결과 위치: {OUTPUT_DIR}')
    print('생성 파일: umap_interactive.html / map_winrate_comparison.html')
    print('          feature_boxplot.html / persona_summary_table.html')

  PUBG 전략 분석 — 핵심 인사이트 요약

[전체 맵 통합 — 페르소나별 우승률]
  🦅 게릴라 운영형             : 13.3%  ██████████████████████████
  🌿 외곽 운영형              : 11.7%  ███████████████████████
  ⚔️ 하이리스크 어태커          : 5.3%  ██████████
  🏃 중앙 점령형              : 2.6%  █████

[맵별 최고 승률 전략]
  Erangel     : 🦅 게릴라 운영형  (14.1%)
  Miramar     : 🌿 외곽 운영형  (13.6%)
  Taego       : 🌿 외곽 운영형  (14.7%)
  Rondo       : 🌿 외곽 운영형  (14.9%)

[실력(데미지) vs 전략(포지셔닝) — 우승 상관관계]
  데미지      x 우승: r=+0.355
  포지셔닝    x 우승: r=-0.105
  분당 킬     x 우승: r=+0.140
  → 실력(데미지)이 우승에 더 큰 영향

[혼합형(uncertain) 현황]
  전체 537,703명 중 207,624명 (38.6%) 분류 불가
  → MARGIN_THRESHOLD=0.5 기준, 낮추면 혼합형 감소

분석 완료. 결과 위치: C:\배그분석\analysis_output
생성 파일: umap_interactive.html / map_winrate_comparison.html
          feature_boxplot.html / persona_summary_table.html
